# Step 00 - Load Data in ADLS Gen2-Backed Delta Lake (Databricks)

Notebook retrieves a dataset from the UC Irvine ML Repository, splits into two subsets for training and holdout, and saves as Delta format in ADLS Gen2.

Logic below to create a mount point in ADLS Gen2 if it doesn't exist - requires having an Azure Service Principal with storage blob data contributor access to the ADLS Gen2 account

### Import packages and load dataset

In [ ]:
from ucimlrepo import fetch_ucirepo 
import pandas as pd
from datetime import datetime
  
# fetch dataset 
power_consumption_of_tetouan_city = fetch_ucirepo(id=849) 
  
# data (as pandas dataframes) 
X = power_consumption_of_tetouan_city.data.features 
y = power_consumption_of_tetouan_city.data.targets 
  
# metadata 
print(power_consumption_of_tetouan_city.metadata) 
  
# variable information 
print(power_consumption_of_tetouan_city.variables) 


{'uci_id': 849, 'name': 'Power Consumption of Tetouan City', 'repository_url': 'https://archive.ics.uci.edu/dataset/849/power+consumption+of+tetouan+city', 'data_url': 'https://archive.ics.uci.edu/static/public/849/data.csv', 'abstract': 'This dataset is related to power consumption of three different distribution networks of Tetouan city which is located in north Morocco.', 'area': 'Social Science', 'tasks': ['Regression'], 'characteristics': ['Multivariate', 'Time-Series'], 'num_instances': 52417, 'num_features': 6, 'feature_types': ['Real', 'Integer'], 'demographics': [], 'target_col': ['Zone 1 Power Consumption', 'Zone 2  Power Consumption', 'Zone 3  Power Consumption'], 'index_col': None, 'has_missing_values': 'no', 'missing_values_symbol': None, 'year_of_dataset_creation': 2018, 'last_updated': 'Fri Mar 08 2024', 'dataset_doi': '10.24432/C5B034', 'creators': ['Abdulwahed Salam', 'Abdelaaziz El Hibaoui'], 'intro_paper': {'title': 'Comparison of Machine Learning Algorithms for the 

In [ ]:
# Assuming power_consumption_of_tetouan_city.data is a valid object with data

X = pd.DataFrame(power_consumption_of_tetouan_city.data.features) 
y= pd.DataFrame(power_consumption_of_tetouan_city.data.targets)

merged_df = pd.concat([X, y], axis=1)
merged_df

DateTime  ...  Zone 3  Power Consumption
0         1/1/2017 0:00  ...                20240.96386
1         1/1/2017 0:10  ...                20131.08434
2         1/1/2017 0:20  ...                19668.43373
3         1/1/2017 0:30  ...                18899.27711
4         1/1/2017 0:40  ...                18442.40964
...                 ...  ...                        ...
52411  12/30/2017 23:10  ...                14780.31212
52412  12/30/2017 23:20  ...                14428.81152
52413  12/30/2017 23:30  ...                13806.48259
52414  12/30/2017 23:40  ...                13512.60504
52415  12/30/2017 23:50  ...                13345.49820

[52416 rows x 9 columns]

### Split dataset into two sections by date

More recent data will be the "hold out" set

In [ ]:
threshold = datetime(2017, 10, 1)

merged_df['DateTime'] = pd.to_datetime(merged_df['DateTime'])

cols = {}
for col in merged_df.columns:
    cols[col] = col.replace(' ', '-')
merged_df.rename(columns=cols, inplace=True)

train_df = merged_df[merged_df['DateTime'] < threshold]
holdout_df = merged_df[merged_df['DateTime'] >= threshold]

train_df


DateTime  ...  Zone-3--Power-Consumption
0     2017-01-01 00:00:00  ...                20240.96386
1     2017-01-01 00:10:00  ...                20131.08434
2     2017-01-01 00:20:00  ...                19668.43373
3     2017-01-01 00:30:00  ...                18899.27711
4     2017-01-01 00:40:00  ...                18442.40964
...                   ...  ...                        ...
39307 2017-09-30 23:10:00  ...                16256.26149
39308 2017-09-30 23:20:00  ...                15973.85087
39309 2017-09-30 23:30:00  ...                15620.83759
39310 2017-09-30 23:40:00  ...                15173.68744
39311 2017-09-30 23:50:00  ...                15120.73544

[39312 rows x 9 columns]

In [ ]:
holdout_df

DateTime  ...  Zone-3--Power-Consumption
39312 2017-10-01 00:00:00  ...                14898.96657
39313 2017-10-01 00:10:00  ...                14531.30699
39314 2017-10-01 00:20:00  ...                14321.21581
39315 2017-10-01 00:30:00  ...                14198.66261
39316 2017-10-01 00:40:00  ...                13889.36170
...                   ...  ...                        ...
52411 2017-12-30 23:10:00  ...                14780.31212
52412 2017-12-30 23:20:00  ...                14428.81152
52413 2017-12-30 23:30:00  ...                13806.48259
52414 2017-12-30 23:40:00  ...                13512.60504
52415 2017-12-30 23:50:00  ...                13345.49820

[13104 rows x 9 columns]

### Create mount point (Databricks to ADLS Gen2) if not exists

In [ ]:
# Set up the configurations
storage_account_name = "..."
container_name = "..."
client_id = "..."
tenant_id = "..."
client_secret = "..."

# Construct the ADLS Gen2 URL
adls_url = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net/"

# Set up the configurations for the mount point
configs = {
    "fs.azure.account.auth.type": "OAuth",
    "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
    "fs.azure.account.oauth2.client.id": client_id,
    "fs.azure.account.oauth2.client.secret": client_secret,
    "fs.azure.account.oauth2.client.endpoint": f"https://login.microsoftonline.com/{tenant_id}/oauth2/token"
}


In [ ]:
# Define the mount point
mount_point = "/mnt/deltalake"

# Unmount if the mount point already exists
if any(mount.mountPoint == mount_point for mount in dbutils.fs.mounts()):
    dbutils.fs.unmount(mount_point)

# Mount the ADLS Gen2 account
dbutils.fs.mount(
    source=adls_url,
    mount_point=mount_point,
    extra_configs=configs
)

# Verify that the mount was successful
# display(dbutils.fs.ls(mount_point))


/mnt/deltalake has been unmounted.


True

### Convert pandas to spark dataframes and save in Delta format to ADLS Gen2

In [ ]:
train_spark_df = df = spark.createDataFrame(train_df)
display(train_spark_df)

DateTime Temperature Humidity Wind-Speed general-diffuse-flows diffuse-flows Zone-1-Power-Consumption Zone-2--Power-Consumption Zone-3--Power-Consumption 2017-01-01T00:00:00Z 6.559 73.8 0.083 0.051 0.119 34055.6962 16128.87538 20240.96386 2017-01-01T00:10:00Z 6.414 74.5 0.083 0.07 0.085 29814.68354 19375.07599 20131.08434 2017-01-01T00:20:00Z 6.313 74.5 0.08 0.062 0.1 29128.10127 19006.68693 19668.43373 2017-01-01T00:30:00Z 6.121 75.0 0.083 0.091 0.096 28228.86076 18361.09422 18899.27711 2017-01-01T00:40:00Z 5.921 75.7 0.081 0.048 0.085 27335.6962 17872.34043 18442.40964 2017-01-01T00:50:00Z 5.853 76.9 0.081 0.059 0.108 26624.81013 17416.41337 18130.12048 2017-01-01T01:00:00Z 5.641 77.7 0.08 0.048 0.096 25998.98734 16993.31307 17945.06024 2017-01-01T01:10:00Z 5.496 78.2 0.085 0.055 0.093 25446.07595 16661.39818 17459.27711 2017-01-01T01:20:00Z 5.678 78.1 0.081 0.066 0.141 24777.72152 16227.35562 17025.54217 2017-01-01T01:30:00Z 5.491 77.3 0.082 0.062 0.111 24279.49367 15939.20973 16794.21687 2017-01-01T01:40:00Z 5.516 77.5 0.081 0.051 0.108 23896.70886 15435.86626 16638.07229 2017-01-01T01:50:00Z 5.471 76.7 0.083 0.059 0.126 23544.3038 15213.37386 16395.18072 2017-01-01T02:00:00Z 5.059 78.6 0.081 0.07 0.096 23003.5443 15169.60486 16117.59036 2017-01-01T02:10:00Z 4.968 78.8 0.084 0.07 0.134 22329.11392 14710.0304 15822.6506 2017-01-01T02:20:00Z 4.975 78.9 0.083 0.055 0.152 22092.1519 14421.8845 15672.28916 2017-01-01T02:30:00Z 4.897 79.1 0.083 0.07 0.096 21903.79747 14104.55927 15597.10843 2017-01-01T02:40:00Z 5.02 79.7 0.081 0.051 0.134 21685.06329 13965.95745 15510.36145 2017-01-01T02:50:00Z 5.407 78.5 0.082 0.062 0.163 21484.55696 13612.15805 15336.86747 2017-01-01T03:00:00Z 5.169 77.9 0.083 0.066 0.108 21107.8481 13535.56231 15140.24096 2017-01-01T03:10:00Z 5.081 77.7 0.084 0.051 0.13 20998.48101 13371.42857 15059.27711 2017-01-01T03:20:00Z 5.041 77.2 0.081 0.062 0.152 20870.88608 13196.35258 15013.01205 2017-01-01T03:30:00Z 5.034 76.9 0.083 0.051 0.185 20870.88608 13167.17325 14897.3494 2017-01-01T03:40:00Z 4.896 76.6 0.085 0.07 0.137 20597.46835 13137.99392 14602.40964 2017-01-01T03:50:00Z 4.805 76.2 0.081 0.059 0.134 20421.26582 12908.20669 14590.84337 2017-01-01T04:00:00Z 4.753 75.7 0.083 0.044 0.134 20524.55696 12820.66869 14585.06024 2017-01-01T04:10:00Z 4.901 74.4 0.083 0.07 0.122 20482.02532 13032.21884 14452.04819 2017-01-01T04:20:00Z 5.203 74.1 0.085 0.062 0.096 20530.63291 12926.44377 14232.28916 2017-01-01T04:30:00Z 5.394 71.9 0.081 0.073 0.1 20512.40506 12948.32827 14157.10843 2017-01-01T04:40:00Z 5.156 74.0 0.079 0.062 0.148 20494.17722 12922.79635 14232.28916 2017-01-01T04:50:00Z 5.179 74.2 0.083 0.037 0.137 20311.89873 12879.02736 14243.85542 2017-01-01T05:00:00Z 4.934 72.9 0.082 0.055 0.134 20542.78481 12806.07903 14243.85542 2017-01-01T05:10:00Z 4.718 75.8 0.08 0.051 0.152 20621.77215 12853.49544 14105.06024 2017-01-01T05:20:00Z 5.546 74.0 0.082 0.055 0.093 20627.8481 12842.55319 14266.98795 2017-01-01T05:30:00Z 4.658 73.5 0.08 0.044 0.104 20797.97468 13137.99392 14353.73494 2017-01-01T05:40:00Z 4.382 76.9 0.081 0.073 0.148 20858.73418 13203.64742 14538.79518 2017-01-01T05:50:00Z 4.212 78.3 0.081 0.117 0.082 21393.41772 13575.68389 14862.6506 2017-01-01T06:00:00Z 4.308 77.2 0.081 0.062 0.126 22219.74684 14068.08511 14908.91566 2017-01-01T06:10:00Z 4.735 74.3 0.08 0.04 0.156 21928.10127 13852.88754 14729.63855 2017-01-01T06:20:00Z 4.769 75.6 0.082 0.099 0.063 21776.20253 13626.74772 14625.54217 2017-01-01T06:30:00Z 4.92 73.7 0.083 0.099 0.096 21654.68354 13582.97872 14480.96386 2017-01-01T06:40:00Z 4.408 76.7 0.082 0.037 0.119 21466.32911 13539.20973 14319.03614 2017-01-01T06:50:00Z 4.29 77.0 0.085 0.033 0.193 20846.58228 12908.20669 14018.31325 2017-01-01T07:00:00Z 4.304 76.0 0.082 0.048 0.152 19983.79747 12342.85714 13492.04819 2017-01-01T07:10:00Z 4.513 74.6 0.084 0.055 0.134 18908.35443 11897.87234 12630.36145 2017-01-01T07:20:00Z 4.489 74.3 0.082 0.081 0.119 18167.08861 11551.36778 11600.96386 2017-01-

In [ ]:
holdout_spark_df = df = spark.createDataFrame(holdout_df)
display(holdout_spark_df)

DateTime Temperature Humidity Wind-Speed general-diffuse-flows diffuse-flows Zone-1-Power-Consumption Zone-2--Power-Consumption Zone-3--Power-Consumption 2017-10-01T00:00:00Z 18.12 87.6 4.916 0.08 0.163 31755.62363 17985.06224 14898.96657 2017-10-01T00:10:00Z 18.0 88.5 4.916 0.055 0.137 31175.84245 17611.61826 14531.30699 2017-10-01T00:20:00Z 18.01 88.4 4.916 0.069 0.148 30154.92341 17148.54772 14321.21581 2017-10-01T00:30:00Z 18.16 88.4 4.914 0.062 0.167 29764.20131 16827.38589 14198.66261 2017-10-01T00:40:00Z 18.18 89.1 4.917 0.051 0.115 29600.35011 16621.9917 13889.3617 2017-10-01T00:50:00Z 18.29 89.0 4.919 0.062 0.133 29304.15755 16312.0332 13831.00304 2017-10-01T01:00:00Z 18.59 89.2 4.913 0.069 0.119 29323.06346 16158.92116 13667.59878 2017-10-01T01:10:00Z 18.75 88.9 4.916 0.073 0.096 28800.0 15848.96266 13661.76292 2017-10-01T01:20:00Z 18.61 88.8 4.917 0.048 0.063 28421.88184 15621.16183 13515.86626 2017-10-01T01:30:00Z 18.74 89.2 4.915 0.073 0.122 28308.44639 15602.48963 13422.4924 2017-10-01T01:40:00Z 18.98 89.4 4.915 0.073 0.115 28245.4267 15404.56432 13171.55015 2017-10-01T01:50:00Z 19.21 89.6 4.914 0.069 0.115 27791.6849 15187.9668 13043.16109 2017-10-01T02:00:00Z 19.28 89.3 4.914 0.073 0.141 27054.35449 15158.09129 12961.45897 2017-10-01T02:10:00Z 19.08 89.7 4.913 0.062 0.144 27174.0919 15008.71369 12949.78723 2017-10-01T02:20:00Z 19.17 89.5 4.916 0.084 0.126 27041.75055 15027.38589 12622.97872 2017-10-01T02:30:00Z 19.26 89.7 4.914 0.11 0.104 27205.60175 14840.6639 12552.94833 2017-10-01T02:40:00Z 19.2 89.6 4.913 0.066 0.133 26934.61707 14762.24066 12319.51368 2017-10-01T02:50:00Z 19.21 89.7 4.914 0.051 0.115 26663.63239 14534.43983 12313.67781 2017-10-01T03:00:00Z 19.12 89.7 4.914 0.066 0.119 26493.47921 14713.69295 12231.97568 2017-10-01T03:10:00Z 19.11 89.8 4.914 0.077 0.174 26493.47921 14373.85892 12307.84195 2017-10-01T03:20:00Z 19.12 89.9 4.914 0.084 0.156 26777.06783 14512.0332 12278.66261 2017-10-01T03:30:00Z 19.06 89.8 4.914 0.077 0.107 26877.89934 14470.95436 12231.97568 2017-10-01T03:40:00Z 19.01 89.9 4.913 0.062 0.1 26865.2954 14676.34855 12185.28875 2017-10-01T03:50:00Z 18.97 90.0 4.913 0.062 0.1 26903.10722 14650.20747 12208.63222 2017-10-01T04:00:00Z 18.69 89.9 4.916 0.08 0.17 27161.48796 14810.78838 12307.84195 2017-10-01T04:10:00Z 17.75 89.4 4.917 0.066 0.107 27060.65646 14512.0332 12477.08207 2017-10-01T04:20:00Z 17.61 89.5 4.915 0.055 0.133 27129.97812 14616.59751 12477.08207 2017-10-01T04:30:00Z 17.69 89.0 4.922 0.077 0.104 27180.39387 14433.60996 12652.15805 2017-10-01T04:40:00Z 17.79 88.7 4.914 0.084 0.159 27186.69584 14639.00415 13048.99696 2017-10-01T04:50:00Z 17.82 88.2 4.917 0.091 0.119 27552.21007 14653.94191 12938.1155 2017-10-01T05:00:00Z 17.83 87.8 4.921 0.062 0.141 26165.77681 14620.33195 12751.36778 2017-10-01T05:10:00Z 17.83 87.3 4.919 0.073 0.107 25737.24289 14321.57676 12500.42553 2017-10-01T05:20:00Z 17.85 87.1 4.917 0.066 0.104 25113.34792 14209.54357 12313.67781 2017-10-01T05:30:00Z 17.97 86.9 4.915 0.051 0.119 24836.06127 13836.09959 11870.15198 2017-10-01T05:40:00Z 18.09 86.5 4.915 0.058 0.148 23575.6674 13163.90041 11414.95441 2017-10-01T05:50:00Z 18.18 86.4 4.917 0.084 0.152 22485.4267 12461.82573 10743.82979 2017-10-01T06:00:00Z 18.12 86.1 4.917 0.062 0.141 22586.25821 12200.41494 9640.851064 2017-10-01T06:10:00Z 18.13 86.1 4.915 0.058 0.096 21659.86871 11468.46473 8549.544073 2017-10-01T06:20:00Z 18.12 85.9 4.915 0.069 0.115 21874.13567 11304.14938 8141.033435 2017-10-01T06:30:00Z 18.1 85.8 4.92 0.08 0.107 22050.59081 11158.50622 8152.705167 2017-10-01T06:40:00Z 17.91 85.4 4.917 0.08 0.163 22327.87746 11251.86722 8106.018237 2017-10-01T06:50:00Z 17.77 85.1 4.914 0.157 0.17 22252.25383 11177.17842 8176.048632 2017-10-01T07:00:00Z 17.81 85.1 4.916 0.717 0.685 22327.87746 11539.41909 8292.765957 2017-10-01T07:10:00Z 17.82 85.0 4.917 2.695 2.271 22636.67396 11513.27801 8467.841945 2017-10-01T07:20:00Z 17.75 84.7 4.918 7.59 6.451 22863.54486 11685.06224 8491.18541 2017-10-01T0

In [ ]:
# Define the output path in ADLS Gen2
output_path = f"{mount_point}/train"

# Save the DataFrame as a Delta table
train_spark_df.write.format("delta").mode("overwrite").save(output_path)

# Confirm the data is saved
display(dbutils.fs.ls(output_path))

path name size modificationTime dbfs:/mnt/deltalake/train/_delta_log/ _delta_log/ 0 1724206223000 dbfs:/mnt/deltalake/train/part-00000-ee2692a6-31cc-4667-ba10-d4f683967640.c000.snappy.parquet part-00000-ee2692a6-31cc-4667-ba10-d4f683967640.c000.snappy.parquet 292832 1724206227000 dbfs:/mnt/deltalake/train/part-00001-07cb4653-210c-45d3-9da1-731b8e9ac26b.c000.snappy.parquet part-00001-07cb4653-210c-45d3-9da1-731b8e9ac26b.c000.snappy.parquet 319747 1724206227000 dbfs:/mnt/deltalake/train/part-00002-94bae8cb-f8bb-4173-8b72-5bee4cdd9bb9.c000.snappy.parquet part-00002-94bae8cb-f8bb-4173-8b72-5bee4cdd9bb9.c000.snappy.parquet 332082 1724206227000 dbfs:/mnt/deltalake/train/part-00003-4cf0ae7c-ee7d-4d27-8f15-4b6d52130951.c000.snappy.parquet part-00003-4cf0ae7c-ee7d-4d27-8f15-4b6d52130951.c000.snappy.parquet 339683 1724206227000

In [ ]:
# Define the output path in ADLS Gen2
output_path = f"{mount_point}/holdout"

# Save the DataFrame as a Delta table
holdout_spark_df.write.format("delta").mode("overwrite").save(output_path)

# Confirm the data is saved
display(dbutils.fs.ls(output_path))

path name size modificationTime dbfs:/mnt/deltalake/holdout/_delta_log/ _delta_log/ 0 1724206259000 dbfs:/mnt/deltalake/holdout/part-00000-e84b6df5-594a-424e-8fd1-a4b3a3712f39.c000.snappy.parquet part-00000-e84b6df5-594a-424e-8fd1-a4b3a3712f39.c000.snappy.parquet 119697 1724206259000 dbfs:/mnt/deltalake/holdout/part-00001-6775cf1e-05c7-462f-8cb6-a17f3ac284fb.c000.snappy.parquet part-00001-6775cf1e-05c7-462f-8cb6-a17f3ac284fb.c000.snappy.parquet 118200 1724206259000 dbfs:/mnt/deltalake/holdout/part-00002-5e72f603-c753-4da5-ad79-012dee035a82.c000.snappy.parquet part-00002-5e72f603-c753-4da5-ad79-012dee035a82.c000.snappy.parquet 118353 1724206259000 dbfs:/mnt/deltalake/holdout/part-00003-2c0013a6-4764-4a6f-bd46-051a1a67ac09.c000.snappy.parquet part-00003-2c0013a6-4764-4a6f-bd46-051a1a67ac09.c000.snappy.parquet 115956 1724206259000

In [ ]:
train_df.head(3).to_dict()

{'DateTime': {0: Timestamp('2017-01-01 00:00:00'),
  1: Timestamp('2017-01-01 00:10:00'),
  2: Timestamp('2017-01-01 00:20:00')},
 'Temperature': {0: 6.559, 1: 6.414, 2: 6.313},
 'Humidity': {0: 73.8, 1: 74.5, 2: 74.5},
 'Wind-Speed': {0: 0.083, 1: 0.083, 2: 0.08},
 'general-diffuse-flows': {0: 0.051, 1: 0.07, 2: 0.062},
 'diffuse-flows': {0: 0.119, 1: 0.085, 2: 0.1},
 'Zone-1-Power-Consumption': {0: 34055.6962, 1: 29814.68354, 2: 29128.10127},
 'Zone-2--Power-Consumption': {0: 16128.87538, 1: 19375.07599, 2: 19006.68693},
 'Zone-3--Power-Consumption': {0: 20240.96386, 1: 20131.08434, 2: 19668.43373}}